In [60]:
import os
import re
import pandas as pd
import numpy as np
from tqdm.auto import tqdm
tqdm.pandas()
import plotly.graph_objects as go

In [38]:
PATH_TO_CSV = 'csv/senkey_data_tutorial.csv'

# 1 

# Грузим таблицу

In [70]:
table = pd.read_csv(PATH_TO_CSV)

In [71]:
table

user_id                event_timestamp  \
0       0003da5682126e66414958d58022fea7  2021-05-21 18:31:09.677163000   
1       0003da5682126e66414958d58022fea7  2021-05-21 18:31:09.677329001   
2       0003da5682126e66414958d58022fea7  2021-05-21 18:31:09.679674004   
3       0003da5682126e66414958d58022fea7  2021-05-21 18:31:09.679818007   
4       0003da5682126e66414958d58022fea7  2021-05-21 18:31:09.688039010   
...                                  ...                            ...   
533552  ffff230563a6c60490c859a8274a7743  2021-05-21 18:30:53.438539025   
533553  ffff230563a6c60490c859a8274a7743  2021-05-21 18:30:53.439606029   
533554  ffff230563a6c60490c859a8274a7743  2021-05-21 18:30:53.440941032   
533555  ffff230563a6c60490c859a8274a7743  2021-05-21 18:30:53.440949033   
533556  ffff230563a6c60490c859a8274a7743  2021-05-21 18:30:53.441369036   

                     event_name  
0                 session_start  
1           app_opened_via_icon  
2                history_opened  
3       sales_category_selected  
4                    app_remove  
...                         ...  
533552       seller_info_opened  
533553       similar_tab_opened  
533554         favorites_opened  
533555         favorites_opened  
533556  sales_category_selected  

[533557 rows x 3 columns]

In [75]:
len(table['event_name'].unique())

41

In [76]:
table['step'].max()

99995

In [77]:
# удалим session_start
table = table[table['event_name'] != 'session_start']

# test

In [78]:
table = table.drop('step', axis=1)

In [79]:
def add_features(df):
    # сортируем по id и времени
    sorted_df = df.sort_values(by=['user_pseudo_id', 'event_timestamp']).copy()
    # добавляем шаги событий
    sorted_df['step'] = sorted_df.groupby('user_pseudo_id').cumcount() + 1
    
    # добавляем узлы-источники и целевые узлы
    # узлы-источники - это сами события, просто переименуем столбец
    sorted_df.rename(columns={'event_name': 'source'}, inplace=True)
    
    # добавляем целевые узлы
    sorted_df['target'] = sorted_df.groupby('user_pseudo_id')['source'].shift(-1)
    
    return sorted_df    

In [80]:
table = add_features(table)

In [81]:
table.head(20)

user_pseudo_id  event_date   event_timestamp  \
1   0003da5682126e66414958d58022fea7    20210524  1621869677329001   
2   0003da5682126e66414958d58022fea7    20210524  1621869679674004   
3   0003da5682126e66414958d58022fea7    20210524  1621869679818007   
4   0003da5682126e66414958d58022fea7    20210524  1621869688039010   
5   00058a2e86c1e535e63b980fbda964b3    20210524  1621829121452000   
6   000928c5f8829c0c88379a49d777559b    20210524  1621885814326000   
7   000a06fcadbc6d04ff46e99ef5528351    20210524  1621840054652000   
9   000fe5214ee3f9842a2d03d7dc28ea41    20210525  1621956232248002   
10  000fe5214ee3f9842a2d03d7dc28ea41    20210525  1621960694128001   
12  000fe5214ee3f9842a2d03d7dc28ea41    20210525  1621960694991004   
14  00110e838aaf7b0b6466a7cb9c2a9065    20210525  1621974194009001   
15  00110e838aaf7b0b6466a7cb9c2a9065    20210525  1621974197138002   
16  00110e838aaf7b0b6466a7cb9c2a9065    20210525  1621974198003005   
17  00110e838aaf7b0b6466a7cb9c2a9065    20210525  1621974200673007   
18  00110e838aaf7b0b6466a7cb9c2a9065    20210525  1621974205313000   
19  00110e838aaf7b0b6466a7cb9c2a9065    20210525  1621974208170000   
20  0012498aca7895dcc5bb9309cf2d142e    20210524  1621806650299000   
22  0017f5327c0d50b6542279e97f704357    20210524  1621864359025001   
23  0017f5327c0d50b6542279e97f704357    20210524  1621864359034000   
24  0017f5327c0d50b6542279e97f704357    20210524  1621864361960006   

                     source  step                   target  
1       app_opened_via_icon     1           history_opened  
2            history_opened     2  sales_category_selected  
3   sales_category_selected     3               app_remove  
4                app_remove     4                      NaN  
5                app_remove     1                      NaN  
6                app_remove     1                      NaN  
7                app_remove     1                      NaN  
9       app_opened_via_icon     1           history_opened  
10           history_opened     2  sales_category_selected  
12  sales_category_selected     3                      NaN  
14      app_opened_via_icon     1           history_opened  
15           history_opened     2  sales_category_selected  
16  sales_category_selected     3          settings_opened  
17          settings_opened     4            aliApp_opened  
18            aliApp_opened     5           history_opened  
19           history_opened     6                      NaN  
20               app_remove     1                      NaN  
22              item_opened     1      app_opened_from_ali  
23      app_opened_from_ali     2     price_history_opened  
24     price_history_opened     3              chart_click

In [10]:
def refresh_steps(df):
    
    new_steps_df = pd.DataFrame(columns=df.columns)
    
    # считаем шаги
    df

    for no, user_id in tqdm(enumerate(df['user_pseudo_id'].unique())):
        # получаем срез данных
        df_temp = df[df['user_pseudo_id'] == user_id].copy().sort_values(by='event_timestamp', ascending=True)
        df_temp['steps_upd'] = list(range(1, len(df_temp) + 1))
        # добавляем источник и цель
        df_temp['source'] = df_temp['event_name'].copy()
        df_temp['target'] = df_temp['source'].shift(-1)
        # добавляем данные
        new_steps_df = pd.concat([new_steps_df, df_temp])
        
        if no % 3000 == 2999:
            # сохраняем
            try:
                saved_df = pd.read_csv('csv/preprocess_data.csv')
                saved_df = pd.concat([saved_df, new_steps_df])
                saved_df.to_csv('csv/preprocess_data.csv', index=False)
                del saved_df
                new_steps_df = pd.DataFrame(columns=df.columns)
            except FileNotFoundError:
                new_steps_df.to_csv('csv/preprocess_data.csv', index=False)
                new_steps_df = pd.DataFrame(columns=df.columns)
                
    # сохраняем
    saved_df = pd.read_csv('csv/preprocess_data.csv')
    saved_df = pd.concat([saved_df, new_steps_df])
    saved_df.to_csv('csv/preprocess_data.csv', index=False)

    return saved_df

In [82]:
% False
try:
    new_steps_df = pd.read_csv('csv/preprocess_data.csv')
except FileNotFoundError:
    new_steps_df = refresh_steps(table)

UsageError: Line magic function `%` not found.


In [83]:
# ограничим количество шагов
STEPS_MAX = 10

df_comp = table[table['step'] <= STEPS_MAX].copy()

In [13]:
def clear_loop(df):
    # удаляем зацикленные связи
    return df[~(df['source'] == df['target'])]

In [14]:
#df_comp = clear_loop(df_comp)

# Создаем source_index

In [87]:
def get_source_index(df):
    res_dict = {}
    
    count = 0
    # получаем индексы источников
    for no, step in tqdm(enumerate(df['step'].unique().tolist())):
        # получаем уникальные наименования для шага
        res_dict[no+1] = {}
        res_dict[no+1]['sources'] = df[df['step'] == step]['source'].unique().tolist()
        res_dict[no+1]['sources_index'] = []
        for i in range(len(res_dict[no+1]['sources'])):
            res_dict[no+1]['sources_index'].append(count)
            count += 1
    return res_dict

In [88]:
source_indexes = get_source_index(df_comp)

0it [00:00, ?it/s]

In [89]:
source_indexes

{1: {'sources': ['app_opened_via_icon',
   'app_remove',
   'item_opened',
   'app_opened_from_ali',
   'first_open',
   'ali_opened_without_referral',
   'history_opened',
   'price_history_opened',
   'sales_category_selected',
   'seller_info_opened',
   'chart_click',
   'reviews_tab_opened',
   'item_loaded_from_store',
   'similar_tab_opened',
   'favorites_opened',
   'aliApp_opened',
   'auth_opened',
   'search_tab_opened',
   'item_info_click',
   'similars_not_fetched_from_server'],
  'sources_index': [0,
   1,
   2,
   3,
   4,
   5,
   6,
   7,
   8,
   9,
   10,
   11,
   12,
   13,
   14,
   15,
   16,
   17,
   18,
   19]},
 2: {'sources': ['history_opened',
   'app_opened_from_ali',
   'sales_category_selected',
   'favorites_opened',
   'item_opened',
   'app_opened_via_icon',
   'ali_opened_without_referral',
   'price_history_opened',
   'search_tab_opened',
   'seller_info_opened',
   'item_loaded_from_store',
   'aliApp_opened',
   'chart_click',
   'item_opened_f

In [90]:
# соединим списки
for key in source_indexes:
    source_indexes[key]['sources_dict'] = {}
    for name, no in zip(source_indexes[key]['sources'], source_indexes[key]['sources_index']):
        source_indexes[key]['sources_dict'][name] = no

# Генерим соответствие цветов меткам

In [124]:
colors = [
    'rgba(42, 157, 143, 1)',
    'rgba(38, 70, 83, 1)',
    'rgba(233, 196, 106, 1)',
    'rgba(244, 162, 97, 1)',
    'rgba(231, 111, 81, 1)',
    'rgba(230, 57, 70, 1)',
    'rgba(168, 218, 220, 1)',
    'rgba(69, 123, 157, 1)',
    'rgba(29, 53, 87, 1)',
    'rgba(107, 112, 92, 1)',
    'rgba(183, 183, 164, 1)',
    'rgba(221, 190, 169, 1)',
    'rgba(142, 202, 230, 1)',
    'rgba(33, 158, 188, 1)',
    'rgba(2, 48, 71, 1)',
    'rgba(255, 183, 3, 1)',
    'rgba(251, 133, 0, 1)',
    'rgba(153, 217, 140, 1)',
    'rgba(118, 200, 147, 1)',
    'rgba(52, 160, 164, 1)',
    'rgba(26, 117, 159, 1)',
    'rgba(247, 37, 133, 1)',
    'rgba(181, 23, 158, 1)',
    'rgba(114, 9, 183, 1)',
    'rgba(86, 11, 173, 1)',
    'rgba(72, 149, 239, 1)',
    'rgba(76, 201, 240, 1)',
    'rgba(242, 132, 130, 1)',
    'rgba(132, 165, 157, 1)',
    'rgba(246, 189, 96, 1)',
    'rgba(187, 62, 3, 1)',
    'rgba(204, 213, 174, 1)',
    'rgba(233, 237, 201, 1)',
    'rgba(254, 250, 224, 1)',
    'rgba(212, 163, 115, 1)',
    'rgba(96, 108, 56, 1)',
    'rgba(40, 54, 24, 1)',
    'rgba(249, 199, 79, 1)',
    'rgba(144, 190, 109, 1)',
    'rgba(67, 170, 139, 1)',
    'rgba(77, 144, 142, 1)',
    'rgba(87, 117, 144, 1)',
    'rgba(39, 125, 161, 1)',
    'rgba(239, 71, 111, 1)',
    'rgba(255, 209, 102, 1)',
    'rgba(6, 214, 160, 1)',
    'rgba(17, 138, 178, 1)',
    'rgba(7, 59, 76, 1)',
    'rgba(0, 53, 102, 1)',
    'rgba(226, 175, 255, 1)',
    'rgba(248, 173, 157, 1)',
    'rgba(211, 211, 211, 1)',
    'rgba(254, 228, 64, 1)',
    'rgba(241, 91, 181, 1)',
    'rgba(155, 93, 229, 1)',
    'rgba(0, 187, 249, 1)',
    'rgba(0, 245, 212, 1)',
    'rgba(130, 192, 204, 1)',
    'rgba(128, 185, 24, 1)',
    'rgba(43, 147, 72, 1)',    
]

In [132]:
colors_dict = {}

In [133]:
#% False
for no, label in enumerate(df_comp['source'].unique()):
    colors_dict[label] = colors[no]

In [134]:
def generate_random_color():
    # сгенерим значение для каждого канала
    r, g, b = np.random.randint(255, size=3)
    return f'rgba({r}, {g}, {b}, 1)'

In [135]:
% False
for label in df_comp['source'].unique():
    colors_dict[label] = generate_random_color()

UsageError: Line magic function `%` not found.


# Создаем словарь с данными

In [136]:
# пересчитаем количестов юзеров в процентах от входа
def percent_users(sources, targets, values):
    # объединим источники и метки и найдем пары
    zip_lists = list(zip(sources, targets, values))
    
    new_list = []
    
    # подготовим список словарь с общим объемом трафика в узлах
    unique_dict = {}
    
    # проходим по каждому узлу
    for source, target, value in zip_lists:
        if source not in unique_dict:
            # находим все источники и считаем общий трафик
            unique_dict[source] = 0
            for sr, tg, vl in zip_lists:
                if sr == source:
                    unique_dict[source] += vl
                    
    # считаем проценты
    for source, target, value in zip_lists:
        new_list.append(round(100 * value / unique_dict[source], 1))
    
    return new_list

In [137]:
def lists_for_plot(source_indexes=source_indexes, colors=colors_dict, frac=10):
    sources = []
    targets = []
    values = []
    labels = []
    link_color = []
    link_text = []

    # проходим по каждому шагу
    for step in tqdm(reversed(sorted(df_comp['step'].unique()))):
        if step + 1 not in source_indexes:
            continue

        # получаем индекс источника
        temp_dict_source = source_indexes[step]['sources_dict']

        # получаем индексы цели
        temp_dict_target = source_indexes[step+1]['sources_dict']

        # проходим по каждой возможной паре, считаем количество таких пар
        for source, index_source in tqdm(temp_dict_source.items()):
            for target, index_target in temp_dict_target.items():
                # делаем срез данных и считаем количество id            
                temp_df = df_comp[(df_comp['step'] == step)&(df_comp['source'] == source)&(df_comp['target'] == target)]
                value = len(temp_df)
                if value > frac:
                    sources.append(index_source)
                    targets.append(index_target)
                    values.append(value)
                    link_color.append(colors[source].replace(', 1)', ', 0.2)'))
                    link_text.append(source + ' --> ' + target)
                    
    labels = []
    colors_labels = []
    for key in source_indexes:
        for name in source_indexes[key]['sources']:
            labels.append(name)
            colors_labels.append(colors[name])
            
    # посчитаем проценты всех потоков
    perc_values = percent_users(sources, targets, values)
    
    # добавим эти проценты в howertext
    new_link_text = []
    for link_tx, perc in zip(link_text, perc_values):
        new_link_text.append(f"{perc}%")
    
    return sources, targets, values, labels, colors_labels, link_color, new_link_text

In [138]:
sources, targets, values, labels, colors_labels, link_color, link_text = lists_for_plot()

0it [00:00, ?it/s]

  0%|          | 0/39 [00:00<?, ?it/s]

  0%|          | 0/37 [00:00<?, ?it/s]

  0%|          | 0/36 [00:00<?, ?it/s]

  0%|          | 0/35 [00:00<?, ?it/s]

  0%|          | 0/35 [00:00<?, ?it/s]

  0%|          | 0/34 [00:00<?, ?it/s]

  0%|          | 0/31 [00:00<?, ?it/s]

  0%|          | 0/28 [00:00<?, ?it/s]

  0%|          | 0/20 [00:00<?, ?it/s]

In [139]:
fig = go.Figure(data=[go.Sankey(
    domain = dict(
      x =  [0,1],
      y =  [0,1]
    ),
    orientation = "h",
    valueformat = ".0f",
    node = dict(
      pad = 50,
      thickness = 15,
      line = dict(color = "black", width = 0.1),
      label = labels,
      color = colors_labels
    ),
    link = dict(
      source = sources, # indices correspond to labels, eg A1, A2, A1, B1, ...
      target = targets,
      value = values,
      #value = perc_values,
      label = link_text,
      color = link_color
  ))])
#fig.update_traces(arrangement='perpendicular')
fig.update_layout(title_text="Aliradar users Sankey Diagram", font_size=10, width=3000, height=1200)
fig.show()

In [27]:
fig.write_html('aliradar_senkey.html', auto_open=True)

In [33]:
df_comp[df_comp['user_pseudo_id'] == 'fff845e0e65479fb5741faa0ede474fb']

user_pseudo_id event_date   event_timestamp step  \
533412  fff845e0e65479fb5741faa0ede474fb   20210525  1621928326093001    1   
533414  fff845e0e65479fb5741faa0ede474fb   20210525  1621928327430002    3   
533415  fff845e0e65479fb5741faa0ede474fb   20210525  1621928329802005    4   
533416  fff845e0e65479fb5741faa0ede474fb   20210525  1621928329808006    5   
533417  fff845e0e65479fb5741faa0ede474fb   20210525  1621928334317010    6   
533418  fff845e0e65479fb5741faa0ede474fb   20210525  1621928334329011    7   
533419  fff845e0e65479fb5741faa0ede474fb   20210525  1621928334342012    8   
533420  fff845e0e65479fb5741faa0ede474fb   20210525  1621928335538016    9   
533421  fff845e0e65479fb5741faa0ede474fb   20210525  1621928335669021   10   
533422  fff845e0e65479fb5741faa0ede474fb   20210525  1621928337605029   11   

                     event_name  steps_upd                   source  \
533412      app_opened_via_icon        1.0      app_opened_via_icon   
533414  sales_category_selected        2.0  sales_category_selected   
533415         favorites_opened        3.0         favorites_opened   
533416         favorites_opened        4.0         favorites_opened   
533417         favorites_opened        5.0         favorites_opened   
533418         favorites_opened        6.0         favorites_opened   
533419         favorites_opened        7.0         favorites_opened   
533420              item_opened        8.0              item_opened   
533421     price_history_opened        9.0     price_history_opened   
533422         favorites_opened       10.0         favorites_opened   

                         target  
533412  sales_category_selected  
533414         favorites_opened  
533415         favorites_opened  
533416         favorites_opened  
533417         favorites_opened  
533418         favorites_opened  
533419              item_opened  
533420     price_history_opened  
533421         favorites_opened  
533422   item_loaded_from_store

In [30]:
df_comp['user_pseudo_id'].unique()

array(['0003da5682126e66414958d58022fea7',
       '00058a2e86c1e535e63b980fbda964b3',
       '000928c5f8829c0c88379a49d777559b', ...,
       'fff845e0e65479fb5741faa0ede474fb',
       'fffc9271396e32f9ee58c69f2b2a7fce',
       'ffff230563a6c60490c859a8274a7743'], dtype=object)

In [36]:
def plot_hist(columns):
    fig = go.Figure(data=[go.Histogram(x=columns)])
    fig.show()

In [37]:
plot_hist(table[table['step'] < 50]['step'])

In [29]:
test_df = df_comp.sort_values(by=['user_pseudo_id', 'event_timestamp'])

In [30]:
test_df

user_pseudo_id  event_date   event_timestamp  step  \
0       0003da5682126e66414958d58022fea7    20210524  1621869677329001     2   
1       0003da5682126e66414958d58022fea7    20210524  1621869679674004     3   
2       0003da5682126e66414958d58022fea7    20210524  1621869679818007     4   
3       0003da5682126e66414958d58022fea7    20210524  1621869688039010     5   
4       00058a2e86c1e535e63b980fbda964b3    20210524  1621829121452000     1   
...                                  ...         ...               ...   ...   
508811  ffff230563a6c60490c859a8274a7743    20210524  1621841563008004     7   
508812  ffff230563a6c60490c859a8274a7743    20210524  1621841595535007     8   
508813  ffff230563a6c60490c859a8274a7743    20210524  1621841595536008     9   
508814  ffff230563a6c60490c859a8274a7743    20210524  1621841595811012    10   
508815  ffff230563a6c60490c859a8274a7743    20210524  1621841597059014    11   

                     event_name  steps_upd                   source  \
0           app_opened_via_icon        1.0      app_opened_via_icon   
1                history_opened        2.0           history_opened   
2       sales_category_selected        3.0  sales_category_selected   
3                    app_remove        4.0               app_remove   
4                    app_remove        1.0               app_remove   
...                         ...        ...                      ...   
508811       similar_tab_opened        6.0       similar_tab_opened   
508812              item_opened        7.0              item_opened   
508813      similar_item_opened        8.0      similar_item_opened   
508814       seller_info_opened        9.0       seller_info_opened   
508815   item_loaded_from_store       10.0   item_loaded_from_store   

                         target  
0                history_opened  
1       sales_category_selected  
2                    app_remove  
3                           NaN  
4                           NaN  
...                         ...  
508811              item_opened  
508812      similar_item_opened  
508813       seller_info_opened  
508814   item_loaded_from_store  
508815          item_info_click  

[131641 rows x 8 columns]

In [35]:
test_df['st'] = test_df.groupby('user_pseudo_id').cumcount() + 1

In [37]:
test_df

user_pseudo_id  event_date   event_timestamp  step  \
0       0003da5682126e66414958d58022fea7    20210524  1621869677329001     2   
1       0003da5682126e66414958d58022fea7    20210524  1621869679674004     3   
2       0003da5682126e66414958d58022fea7    20210524  1621869679818007     4   
3       0003da5682126e66414958d58022fea7    20210524  1621869688039010     5   
4       00058a2e86c1e535e63b980fbda964b3    20210524  1621829121452000     1   
...                                  ...         ...               ...   ...   
508811  ffff230563a6c60490c859a8274a7743    20210524  1621841563008004     7   
508812  ffff230563a6c60490c859a8274a7743    20210524  1621841595535007     8   
508813  ffff230563a6c60490c859a8274a7743    20210524  1621841595536008     9   
508814  ffff230563a6c60490c859a8274a7743    20210524  1621841595811012    10   
508815  ffff230563a6c60490c859a8274a7743    20210524  1621841597059014    11   

                     event_name  steps_upd                   source  \
0           app_opened_via_icon        1.0      app_opened_via_icon   
1                history_opened        2.0           history_opened   
2       sales_category_selected        3.0  sales_category_selected   
3                    app_remove        4.0               app_remove   
4                    app_remove        1.0               app_remove   
...                         ...        ...                      ...   
508811       similar_tab_opened        6.0       similar_tab_opened   
508812              item_opened        7.0              item_opened   
508813      similar_item_opened        8.0      similar_item_opened   
508814       seller_info_opened        9.0       seller_info_opened   
508815   item_loaded_from_store       10.0   item_loaded_from_store   

                         target  st  
0                history_opened   1  
1       sales_category_selected   2  
2                    app_remove   3  
3                           NaN   4  
4                           NaN   1  
...                         ...  ..  
508811              item_opened   6  
508812      similar_item_opened   7  
508813       seller_info_opened   8  
508814   item_loaded_from_store   9  
508815          item_info_click  10  

[131641 rows x 9 columns]

In [41]:
test_df.groupby('user_pseudo_id')['event_name'].shift(-1)

0                  history_opened
1         sales_category_selected
2                      app_remove
3                             NaN
4                             NaN
                   ...           
508811                item_opened
508812        similar_item_opened
508813         seller_info_opened
508814     item_loaded_from_store
508815                        NaN
Name: event_name, Length: 131641, dtype: object

array([235,  65,   5])